# LLM Abliterate v1.2 script, adapted for google/abliterate-gemma-2-27b (uses bartowski's gguf for llama.cpp)

Author: byroneverson

This script ran at kaggle.com, accelerator: None, persistence: Files only

# Download bartowski/gemma-2-27b-it-GGUF gemma-2-27b-it-Q4_K_M.gguf locally

Using smallest quant for now to test method and will try q8 first when method works to see if kaggle had the memory for it

In [6]:
%cd /kaggle/working

from huggingface_hub import hf_hub_download

hf_hub_download(repo_id="bartowski/gemma-2-27b-it-GGUF", filename="gemma-2-27b-it-Q4_K_M.gguf", local_dir="/kaggle/working")

/kaggle/working


gemma-2-27b-it-Q4_K_M.gguf:   0%|          | 0.00/16.6G [00:00<?, ?B/s]

'/kaggle/working/gemma-2-27b-it-Q4_K_M.gguf'

# Download original abliterator script for harmful and harmless instructions txt files
Credit: https://github.com/Sumandora/remove-refusals-with-transformers

Temporary: We need my fork of ggml-python because the official abetlen is out of date and ggml_tensor is incompatible at the moment 

In [10]:
%cd /kaggle/working
!git clone https://github.com/Sumandora/remove-refusals-with-transformers.git
!git clone --recurse-submodules https://github.com/byroneverson/ggml-python.git

/kaggle/working
fatal: destination path 'remove-refusals-with-transformers' already exists and is not an empty directory.
Cloning into 'llama-cpp-python'...
remote: Enumerating objects: 8183, done.
remote: Counting objects: 100% (2406/2406), done.
remote: Compressing objects: 100% (302/302), done.
remote: Total 8183 (delta 2294), reused 2118 (delta 2099), pack-reused 5777 (from 1)
Receiving objects: 100% (8183/8183), 2.00 MiB | 10.17 MiB/s, done.
Resolving deltas: 100% (5349/5349), done.
Submodule 'vendor/llama.cpp' (https://github.com/ggerganov/llama.cpp.git) registered for path 'vendor/llama.cpp'
Cloning into '/kaggle/working/llama-cpp-python/vendor/llama.cpp'...
remote: Enumerating objects: 32639, done.        
remote: Counting objects: 100% (11531/11531), done.        
remote: Compressing objects: 100% (805/805), done.        
remote: Total 32639 (delta 11183), reused 10777 (delta 10724), pack-reused 21108 (from 1)        
Receiving objects: 100% (32639/32639), 56.23 MiB | 22.56 Mi

# Install my ggml-python and normal llama-cpp-python

In [1]:
%cd /kaggle/working

!pip install ./ggml-python
!pip install llama-cpp-python
!pip install jaxtyping
!pip install einops

/kaggle/working
Processing ./ggml-python
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for ggml_python: filename=ggml_python-0.0.37-cp310-cp310-linux_x86_64.whl size=702614 sha256=ef43a72a325d5a8510261b569a33f5daefd9089ffab3dde08c0d76bfcf5780e4
  Stored in directory: /root/.cache/pip/wheels/2c/e9/79/52a1e26e8ea183251d8785ae5d126df25b8aa30fddf1e13f32
Successfully built ggml_python
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.3/64.3 MB 20.7 MB/s eta 0:00:0000:0100:01
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.5/45.5 kB 1.5 MB/s eta 0:00:00
  Created wheel for llama-cpp-python: filename=llama_cpp_python-0.2.89-cp310-cp310-linux_x86_64.whl size=3292280 sha256=4c

# Obtain estimated refusal direction vector

Determine the layer where the model has sufficiently developed a sense of difference between the harmful and harmless.

It seems that larger models still should have this done at a similar layer as smaller ones.

For models with hidden_size of 4096 and intermediate size ~14k, this is roughly layer 19 or 20 regardless of layer count.

TODO: Perform PCA (Principal component analysis) in a separate step to help detect which layer(s) are ideal.

In [28]:
%cd /kaggle/working

import ctypes
import os
import multiprocessing
import random
import gc
import sys

# llama.cpp/GGML library
import llama_cpp
import ggml

# Easy tensor handling
import torch
from math import prod

from tqdm import tqdm

# Number of total layers in your model
total_layers = 40
target_percent = 0.5 # 50% through the layers
target_index = int(total_layers * target_percent)

# Number of instructions to average for our feature estimation (e.g. 512 for harmful and 512 for harmless)
instructions = 64 #512

# Our local gguf model
# TODO: Load model with only num_layers we actually need for this step
local_repo_dir = "/kaggle/working"
model_path = local_repo_dir + "/" + "gemma-2-27b-it-Q4_K_M.gguf"

# Init llama backend
llama_cpp.llama_backend_init(numa=False)

# llama.cpp custom model code

def c_array_to_tensor(pointer, shape, torch_type):
    arr = (pointer._type_ * prod(shape)).from_address(
    ctypes.addressof(pointer.contents))
    return torch.frombuffer(arr, dtype=torch_type).view(*shape)

def model_load(model_path):
    # TODO: Attempt to hook num_layers
    model_params = llama_cpp.llama_model_default_params()
    model_params.n_gpu_layers = 0
    model_params.use_mmap = True
    model = llama_cpp.llama_load_model_from_file(model_path.encode("utf-8"), model_params)
    
    return model

def model_free(model):
    llama_cpp.llama_free(model)

def model_apply_chat_template(model, role, content, add_assistant=True):
    chat_message = llama_cpp.llama_chat_message(role=role.encode("utf-8"), content=content.encode("utf-8"))
    buffer_length = len(content) * 2
    buffer = ctypes.create_string_buffer(buffer_length)
    result = llama_cpp.llama_chat_apply_template(model, None, ctypes.pointer(chat_message), 1, add_assistant, buffer, ctypes.c_int32(buffer_length))
    if result <= 0:
        return input_str
    elif result >= buffer_length:
        buffer_length = result + 1
        buffer = ctypes.create_string_buffer(buffer_length)
        result = llama_cpp.llama_chat_apply_template(model, None, ctypes.pointer(chat_message), 1, add_assistant, buffer, ctypes.c_int32(buffer_length))
    if result > 0:
        return buffer.value.decode("utf-8")
    else:
        return content
    
def model_tokenize(model, prompt):
    prompt_count = len(prompt.encode('utf-8'))
    if prompt_count == 0:
        return []

    tokens = (ctypes.c_int32 * prompt_count)()
    count = llama_cpp.llama_tokenize(model, 
                                     prompt.encode('utf-8'), 
                                     ctypes.c_int32(prompt_count), 
                                     tokens, 
                                     ctypes.c_int32(prompt_count), 
                                     True, 
                                     True)
    if prompt_count > count:
        tokens = tokens[:count]
    return tokens

# Callback should fill this as the model runs
# 2 tensors for input embedding
# 40 tensors per layer

def print_tensor_info(t_ptr):
     #: contiguous: {ggml.ggml_is_contiguous(t)}, permuted: {ggml.ggml_is_permuted(t)}, transposed: {ggml.ggml_is_transposed(t)}"
    t = t_ptr.contents
    print(f"{ggml.ggml_type_name(t.type)} {ggml.ggml_op_desc(t_ptr)} {t.name}")
    print(f"  n_elements = {ggml.ggml_nelements(t)}")
    print(f"  ne         = ({t.ne[0]}, {t.ne[1]}, {t.ne[2]}, {t.ne[3]})")
    print(f"  nb         = ({t.nb[0]}, {t.nb[1]}, {t.nb[2]}, {t.nb[3]})")
    is_host = ggml.ggml_backend_buffer_is_host(t.buffer)
    print(f"  is_host    = {is_host}")
    print(f"  buffer     = {t.buffer}")
    print(f"  data       = {t.data}")
    if ctypes.c_void_p.from_buffer(t.src[0]).value != None:
        print(f"  src[0]     = {ggml.ggml_op_desc(t.src[0])}")
    if ctypes.c_void_p.from_buffer(t.src[1]).value != None:
        print(f"  src[1]     = {ggml.ggml_op_desc(t.src[1])}")

c_abort_callback = ctypes.CFUNCTYPE(
    ctypes.c_bool, ctypes.c_void_p
)(abort_callback)

class CallbackDataStruct(ctypes.Structure):
    _fields_ = [
        ("layer_tensor_count", ctypes.c_int),
        ("layer_index", ctypes.c_int),
        ("target_index", ctypes.c_int),
        ("tensor_index", ctypes.c_int),
        ("tensor", ctypes.c_void_p)
    ]

callback_data = CallbackDataStruct()
callback_data.target_index = 20 #target_index
callback_data.layer_tensor_count = 40
callback_data.layer_index = -1
callback_data.tensor_index = 0
callback_data.tensor = 0

def hidden_states_eval_callback(t_void_p, ask, user_data):
    cb_data_ptr = ctypes.cast(user_data, ctypes.POINTER(CallbackDataStruct))
    cb_data = cb_data_ptr.contents
    t_ptr = ctypes.cast(t_void_p, ctypes.POINTER(ggml.ggml_tensor))
    t = t_ptr.contents
    if ask:
        #print(f"{ggml.ggml_type_name(t.type)} {ggml.ggml_op_desc(t_ptr)} {t.name} ({t.ne[0]}, {t.ne[1]})")
        index = cb_data.tensor_index
        cb_data.tensor_index += 1
        if index % cb_data.layer_tensor_count == 1: #1
            layer_index = cb_data.layer_index
            cb_data.layer_index += 1
            if layer_index >= -1:
                sys.stdout.flush()
                if layer_index == cb_data.target_index:
                    #print(f"Target layer {layer_index}, tensor {index}")
                    # Request data next callback
                    return True
    else:
        cb_data.tensor = t_void_p
        #print_tensor_info(t_ptr)
        sys.stdout.flush()
        
        # Returning false should stop graph in it's tracks without error, this may let us get the current progress in embeddings?
        return False #True # Continue graph
    # return True to request data next callback, false to skip, ask will be False when returning data from a request
    return False

c_hidden_states_eval_callback = ctypes.CFUNCTYPE(
    ctypes.c_bool, ctypes.c_void_p, ctypes.c_bool, ctypes.c_void_p
)(hidden_states_eval_callback)   

def model_generate_hidden_states(model, prompt, n_predict=1):
    # Reset callbacks count
    callback_data.layer_index = -1
    callback_data.tensor_index = 0
    
    # Start with no past
    n_past = 0
    
    # Reset hidden_states
    hidden_states = []
    
    #DEBUG
    #prompt = "Test?"
    
    # Chat template
    prompt = model_apply_chat_template(model, 
                                       role="user", 
                                       content=prompt, 
                                       add_assistant=True)
    
    # Add space for llama only, check model params for add space var
    add_space = False # FIX
    if add_space:
        prompt = b" " + prompt
    
    toks = model_tokenize(model, prompt)
    n_tokens = len(toks)
    #print(prompt)
    #print(n_tokens)
    #print(toks)

    # Clear cache per example
    llama_cpp.llama_kv_cache_clear(context)
    
    # Fill batch
    batch.n_tokens = n_tokens
    for i in range(n_tokens):
        batch.token[i] = toks[i]
        batch.pos[i] = i
        batch.seq_id[i][0] = 0
        batch.n_seq_id[i] = 1
        batch.logits[i] = False
    batch.logits[n_tokens - 1] = True
    
    # Decode batch
    result = llama_cpp.llama_decode(context, batch)
    if result == 1:
        print("decode warning")
    elif result < 0:
        print("decode error")
    sys.stdout.flush()

    # Get data from tensor
    t_ptr = ctypes.cast(callback_data.tensor, ctypes.POINTER(ggml.ggml_tensor))
    #print_tensor_info(t_ptr)
    data = ctypes.cast(t_ptr.contents.data, ctypes.POINTER(ctypes.c_float))
    n_elements = ggml.ggml_nelements(t_ptr)
    n_embd = llama_cpp.llama_n_embd(model)
    
    # Convert float buffer to torch array for easy handling
    hidden_state = c_array_to_tensor(data, (n_elements // n_embd, n_embd), torch.float32)
    #print(type(hidden_state))
    #print(hidden_state.shape)
    #print(hidden_state)
    #print(hidden_state[0])
    #sys.stdout.flush()
    return hidden_state[-1]

# Clear memory of past model usage
model = None
gc.collect()

# Load model
model = model_load(model_path)

print("Instruction count: " + str(instructions))
print("Target layer index: " + str(target_index))

with open("./remove-refusals-with-transformers/harmful.txt", "r") as f:
    harmful = f.readlines()

with open("./remove-refusals-with-transformers/harmless.txt", "r") as f:
    harmless = f.readlines()

harmful_instructions = random.sample(harmful, instructions)
harmless_instructions = random.sample(harmless, instructions)

gc.collect()

# Generate target layer hidden state files for harmful and harmless features
def save_target_hidden_states(prompt, index, feature):
    bar.update(n=1)
    
    # Generates using each example, cache is disables so it doesn't keep previous examples in it's context, obviously we need to output the full states
    # It would be ideal if we could have it output the states for only the layer we want
    output = model_generate_hidden_states(model, prompt)
    # We still select the target layers, then only keep the hidden state of the last token (-1 part)
    hidden = output #output.hidden_states[0][target_index][:, -1, :]
    # Save each hidden state to disk to keep memory usage at a minimum
    dir_path = local_repo_dir + "/" + feature + "_states"
    file_path = dir_path + "/" + str(index) + ".pt"
    if not os.path.exists(dir_path):
        os.makedirs(dir_path)
    torch.save(hidden, file_path)

# Create context
context_params = llama_cpp.llama_context_default_params()
n_threads = multiprocessing.cpu_count()
context_params.n_threads = n_threads
context_params.n_threads_batch = n_threads
context_params.seed  = 1234
context_params.cb_eval = c_hidden_states_eval_callback
context_params.cb_eval_user_data = ctypes.cast(ctypes.pointer(callback_data), ctypes.c_void_p)
context = llama_cpp.llama_new_context_with_model(model, context_params)

# Create batch
batch = llama_cpp.llama_batch_init(context_params.n_batch, 0, context_params.n_ctx)

# Progress bar

import time
time.sleep(5) # Let model finish printing before start
sys.stdout.flush()
max_its = instructions * 2
bar = tqdm(total=max_its)

# Save harmful states
for index, instruction in enumerate(harmful_instructions):
    save_target_hidden_states(instruction, index, "harmful")

# Save harmless states
for index, instruction in enumerate(harmless_instructions):
    save_target_hidden_states(instruction, index, "harmless")

bar.close()

# Clear memory of model usage
# Free batch, model, context, and backend
llama_cpp.llama_batch_free(batch)
llama_cpp.llama_free(context)
llama_cpp.llama_free_model(model)
llama_cpp.llama_backend_free()

model = None
context = None
harmful_instructions = None
harmless_instructions = None
gc.collect()

# Load the hidden state of an instruction for a specific feature
def load_target_hidden_state(feature, index):
    file_path = local_repo_dir + "/" + feature + "_states" + "/" + str(index) + ".pt"
    return torch.load(file_path)

# Get the means of harmful states
harmful_hidden = [load_target_hidden_state("harmful", i) for i in range(instructions)]
harmful_mean = torch.stack(harmful_hidden).mean(dim=0)             

harmful_hidden = None
gc.collect()

# Get the means of harmless states
harmless_hidden = [load_target_hidden_state("harmless", i) for i in range(instructions)]
harmless_mean = torch.stack(harmless_hidden).mean(dim=0)             

harmful_hidden = None
gc.collect()
        
# Get refusal direction tensor and save it to disk
refusal_direction = harmful_mean - harmless_mean
refusal_direction = refusal_direction / refusal_direction.norm()
print(refusal_direction)
local_repo_dir = "/kaggle/working/gemma-2-27b-it"
if not os.path.exists(local_repo_dir):
    os.makedirs(local_repo_dir)
torch.save(refusal_direction, local_repo_dir + "/" + "refusal_direction.pt")

# Clean-up
harmful_hidden = None
harmless_hidden = None
gc.collect()

llama_model_loader: loaded meta data with 33 key-value pairs and 508 tensors from /kaggle/working/gemma-2-27b-it-Q4_K_M.gguf (version GGUF V3 (latest))
llama_model_loader: Dumping metadata keys/values. Note: KV overrides do not apply in this output.
llama_model_loader: - kv   0:                       general.architecture str              = gemma2
llama_model_loader: - kv   1:                               general.name str              = gemma-2-27b-it
llama_model_loader: - kv   2:                      gemma2.context_length u32              = 8192
llama_model_loader: - kv   3:                    gemma2.embedding_length u32              = 4608
llama_model_loader: - kv   4:                         gemma2.block_count u32              = 46
llama_model_loader: - kv   5:                 gemma2.feed_forward_length u32              = 36864
llama_model_loader: - kv   6:                gemma2.attention.head_count u32              = 32
llama_model_loader: - kv   7:             gemma2.attention.hea

/kaggle/working


llama_model_loader: - kv  18:                      tokenizer.ggml.scores arr[f32,256000]  = [-1000.000000, -1000.000000, -1000.00...
llama_model_loader: - kv  19:                  tokenizer.ggml.token_type arr[i32,256000]  = [3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, ...
llama_model_loader: - kv  20:                tokenizer.ggml.bos_token_id u32              = 2
llama_model_loader: - kv  21:                tokenizer.ggml.eos_token_id u32              = 1
llama_model_loader: - kv  22:            tokenizer.ggml.unknown_token_id u32              = 3
llama_model_loader: - kv  23:            tokenizer.ggml.padding_token_id u32              = 0
llama_model_loader: - kv  24:               tokenizer.ggml.add_bos_token bool             = true
llama_model_loader: - kv  25:               tokenizer.ggml.add_eos_token bool             = false
llama_model_loader: - kv  26:                    tokenizer.chat_template str              = {{ bos_token }}{% if messages[0]['rol...
llama_model_loader: - kv  27: 

Instruction count: 64
Target layer index: 20


llama_new_context_with_model: n_ctx      = 512
llama_new_context_with_model: n_batch    = 512
llama_new_context_with_model: n_ubatch   = 512
llama_new_context_with_model: flash_attn = 0
llama_new_context_with_model: freq_base  = 10000.0
llama_new_context_with_model: freq_scale = 1
llama_kv_cache_init:        CPU KV buffer size =   184.00 MiB
llama_new_context_with_model: KV self size  =  184.00 MiB, K (f16):   92.00 MiB, V (f16):   92.00 MiB
llama_new_context_with_model:        CPU  output buffer size =     0.98 MiB
llama_new_context_with_model:        CPU compute buffer size =   509.00 MiB
llama_new_context_with_model: graph nodes  = 1850
llama_new_context_with_model: graph splits = 1
100%|██████████| 128/128 [16:51<00:00,  7.90s/it]
/tmp/ipykernel_36/504046463.py:321: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbi

tensor([-1.1803e-02, -2.3992e-03,  6.0799e-03,  ..., -3.0787e-05,
        -5.7875e-04, -1.0906e-02])


0

# Remove temporary harmful and harmless hidden state files

In [10]:
%cd /kaggle/working/glm-4-9b-chat
!rm -r ./harmless_states
!rm -r ./harmful_states

/kaggle/working/glm-4-9b-chat


/opt/conda/lib/python3.10/pty.py:89: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  pid, fd = os.forkpty()


# Modify individual safetensors files separately to save memory

To save space in kaggle, I will download each split separately and patch it, then upload it to my own repo.

All of the smaller files will be uploaded as a folder.

Be sure to change the repo to your newly created huggingface repo and set all your kaggle secrets for reading and writing to hf!

In [ ]:
%cd /kaggle/working

import gc
gc.collect()

from safetensors import safe_open
from safetensors.torch import save_file
from typing import Optional, Tuple

import einops
import jaxtyping
import torch

from huggingface_hub import hf_hub_download
from huggingface_hub import upload_folder
from huggingface_hub import upload_file

from transformers import AutoConfig

local_repo_dir = "/kaggle/working/gemma-2-27b-it"

repo_id = "byroneverson/gemma-2-27b-it-abliterated"

from kaggle_secrets import UserSecretsClient

user_secrets = UserSecretsClient()
read_token = user_secrets.get_secret("hf_read")
write_token = user_secrets.get_secret("hf_write")

# Download necessary files
try:
    for filename in ["config.json", 
                     "generation_config.json",
                     "model.safetensors.index.json", 
                     "special_tokens_map.json", 
                     "tokenizer.json", 
                     "tokenizer.model", 
                     "tokenizer_config.json"]:
        hf_hub_download(repo_id="google/gemma-2-27b-it", filename=filename, local_dir=local_repo_dir, use_auth_token=read_token)
except Exception as e:
    print(f"Error downloading {filename}: {e}")

# Upload smaller files first
try:
    upload_folder(folder_path=local_repo_dir, repo_id=repo_id, token=write_token)
except Exception as e:
    print(f"Error uploading folder: {e}")

config = AutoConfig.from_pretrained(local_repo_dir, local_files_only=True, trust_remote_code=True)
refusal_direction = torch.load(local_repo_dir + "/" + "refusal_direction.pt").to(torch.float32)

def orthogonalize_matrix(matrix: jaxtyping.Float[torch.Tensor, "... d"], 
                        direction: jaxtyping.Float[torch.Tensor, "d"]) -> jaxtyping.Float[torch.Tensor, "... d"]:
    proj = einops.einsum(matrix, direction.view(-1, 1), "... d, d single -> ... single") * direction
    return matrix - proj

def load_safetensors_file(file_path):
    """Loads a single safetensors file into a dictionary of tensors.
    Args:
        file_path (str): Path to the safetensors file.
    Returns:
        dict: A dictionary containing the loaded tensors.
    """
    tensors = {}
    with safe_open(file_path, framework="pt", device="cpu") as f:
        #print(f.metadata())
        for key in f.keys():
            tensors[key] = f.get_tensor(key)
    return tensors

# Make sure safetensors count matches the actual count for the model you are modifying
safetensors_count = 12
device = refusal_direction.device
# TODO: Add in skip start and end layers logic
#       I forgot to in v1.0 but the abliterated output model still worked great so I didn't even notice
for idx in range(safetensors_count):
    gc.collect()
    
    filename = "model-" + str(idx + 1).zfill(5) + "-of-" + str(safetensors_count).zfill(5) + ".safetensors"
    print(filename)
    
    # Download file 
    temp_dir = "/kaggle/temp"
    hf_hub_download(repo_id="google/gemma-2-27b-it", filename=filename, local_dir=temp_dir, use_auth_token=read_token)
    
    file_path = temp_dir + "/" + filename
    tensors = load_safetensors_file(file_path)
    
    for tensor in tensors:
        # tok_embeddings
        if ".embed_tokens.weight" in tensor:
            print("• " + tensor)
            dtype = tensors[tensor].dtype
            t = tensors[tensor].to(torch.float32).to(device)
            tensors[tensor].copy_(orthogonalize_matrix(t, refusal_direction).to(dtype))
            t = []
        
        # attention.wo
        if ".self_attn.o_proj.weight" in tensor:
            print("• " + tensor)
            dtype = tensors[tensor].dtype
            t = tensors[tensor].to(torch.float32).to(device)
            t_rearranged = einops.rearrange(t, "m (n h) -> n h m", n=config.num_attention_heads).to(device)
            t_orthogonalized = orthogonalize_matrix(t_rearranged, refusal_direction)
            t_rearranged = einops.rearrange(t_orthogonalized, "n h m -> m (n h)", n=config.num_attention_heads)
            tensors[tensor].copy_(t_rearranged.to(dtype))
            t = []
            t_rearranged = []
            t_orthogonalized = []
        
        # feed_forward.w2
        if ".mlp.down_proj.weight" in tensor:
            print("• " + tensor)
            dtype = tensors[tensor].dtype
            t = tensors[tensor].to(torch.float32).to(device)
            t_transposed = t.T.to(device)
            t_orthogonalized = orthogonalize_matrix(t_transposed, refusal_direction)
            t_transposed = t_orthogonalized.T
            tensors[tensor].copy_(t_transposed.to(dtype))
            t = []
            t_transposed = []
            t_orthogonalized = []
            
    # Save file
    save_file(tensors, file_path, metadata={'format': 'pt'})
    
    # Upload file to your repo
    upload_file(path_or_fileobj=file_path, path_in_repo=filename, repo_id=repo_id, token=write_token)
    
    import os
    if os.path.exists(file_path):
        os.remove(file_path)
    else:
        print("Remove error: The file does not exist")

# Patching done
print("done!")


# Use GGUF My Repo space on HF to convert abliterated model back to GGUF

# Test in your favorite llama.cpp environment